In [1]:
import matplotlib
from matplotlib import pyplot as plt

import numpy as np
from numpy import linalg as LA
import cv2
import math

import plotly
from plotly.graph_objs import *
from plotly.offline import download_plotlyjs, init_notebook_mode, iplot
from plotly import tools

import time
import collections as col
from collections import OrderedDict

import ast
from ndreg import *
import ndio.remote.neurodata as neurodata

import nibabel as nib
import networkx as nx
import re
import pandas as pd
import requests
import json
import seaborn as sns
import csv, gc

from sklearn.manifold import spectral_embedding as se

import scipy.sparse as sp

plotly.offline.init_notebook_mode()

In [3]:
fear = nx.read_graphml("Fear199.graphml")

In [4]:
print(fear.nodes())

['[110, 57, 308]', '[301, 157, 231]', '[124, 199, 334]', '[306, 160, 290]', '[125, 84, 401]', '[261, 209, 383]', '[201, 99, 128]', '[164, 173, 347]', '[192, 261, 446]', '[272, 112, 70]', '[170, 85, 360]', '[139, 176, 515]', '[362, 219, 307]', '[184, 154, 318]', '[403, 92, 360]', '[303, 216, 399]', '[163, 276, 402]', '[306, 230, 419]', '[215, 249, 264]', '[420, 152, 288]', '[65, 217, 262]', '[121, 203, 191]', '[303, 231, 199]', '[219, 203, 63]', '[358, 207, 221]', '[221, 222, 325]', '[325, 261, 301]', '[110, 74, 178]', '[136, 167, 446]', '[132, 132, 480]', '[199, 158, 160]', '[144, 160, 56]', '[142, 248, 225]', '[107, 195, 198]', '[312, 135, 362]', '[192, 83, 230]', '[290, 230, 363]', '[344, 128, 262]', '[269, 150, 375]', '[373, 181, 208]', '[378, 214, 201]', '[84, 115, 158]', '[248, 153, 425]', '[287, 223, 238]', '[254, 108, 295]', '[300, 115, 370]', '[207, 84, 120]', '[295, 25, 289]', '[313, 183, 475]', '[183, 123, 126]', '[160, 75, 290]', '[315, 39, 245]', '[332, 65, 287]', '[226, 16

In [9]:
print(fear.node['[110, 57, 308]']['coord'])

[110, 57, 308]


In [7]:
print(fear.nodes(data=True))

[('[110, 57, 308]', {'intensity': 105, 'region': 635, 'coord': u'[110, 57, 308]'}), ('[301, 157, 231]', {'intensity': 114, 'region': 672, 'coord': u'[301, 157, 231]'}), ('[124, 199, 334]', {'intensity': 63, 'region': 504, 'coord': u'[124, 199, 334]'}), ('[306, 160, 290]', {'intensity': 502, 'region': 733, 'coord': u'[306, 160, 290]'}), ('[125, 84, 401]', {'intensity': 54, 'region': 33, 'coord': u'[125, 84, 401]'}), ('[261, 209, 383]', {'intensity': 67, 'region': 146, 'coord': u'[261, 209, 383]'}), ('[201, 99, 128]', {'intensity': 52, 'region': 1015, 'coord': u'[201, 99, 128]'}), ('[164, 173, 347]', {'intensity': 43, 'region': 128, 'coord': u'[164, 173, 347]'}), ('[192, 261, 446]', {'intensity': 58, 'region': 136, 'coord': u'[192, 261, 446]'}), ('[272, 112, 70]', {'intensity': 44, 'region': 0, 'coord': u'[272, 112, 70]'}), ('[170, 85, 360]', {'intensity': 51, 'region': 842, 'coord': u'[170, 85, 360]'}), ('[139, 176, 515]', {'intensity': 64, 'region': 10681, 'coord': u'[139, 176, 515]'})

# Getting subgraph of one region

In [11]:
# Getting a subgraph of all the nodes with a certain region
sg = fear.subgraph([n for n, attrdict in fear.node.items() if attrdict['region'] == 635])

In [13]:
print(sg.nodes(data=True))

[('[122, 44, 317]', {'intensity': 100, 'region': 635, 'coord': u'[122, 44, 317]'}), ('[329, 48, 308]', {'intensity': 172, 'region': 635, 'coord': u'[329, 48, 308]'}), ('[110, 57, 308]', {'intensity': 105, 'region': 635, 'coord': u'[110, 57, 308]'}), ('[283, 34, 302]', {'intensity': 85, 'region': 635, 'coord': u'[283, 34, 302]'}), ('[311, 38, 305]', {'intensity': 127, 'region': 635, 'coord': u'[311, 38, 305]'}), ('[143, 41, 310]', {'intensity': 119, 'region': 635, 'coord': u'[143, 41, 310]'}), ('[384, 89, 372]', {'intensity': 76, 'region': 635, 'coord': u'[384, 89, 372]'})]


In [35]:
total = np.array([0,0,0])
for node in sg.node:
    s = sg.node[node]['coord']
    coord = ast.literal_eval(s) # convert string of list to list
    coord = np.array(coord)
    total += coord

centroid = total / float(nx.number_of_nodes(sg))

In [36]:
print(centroid)

[ 240.28571429   50.14285714  317.42857143]


In [18]:
print(sg.node)

{'[122, 44, 317]': {'intensity': 100, 'region': 635, 'coord': u'[122, 44, 317]'}, '[329, 48, 308]': {'intensity': 172, 'region': 635, 'coord': u'[329, 48, 308]'}, '[110, 57, 308]': {'intensity': 105, 'region': 635, 'coord': u'[110, 57, 308]'}, '[283, 34, 302]': {'intensity': 85, 'region': 635, 'coord': u'[283, 34, 302]'}, '[311, 38, 305]': {'intensity': 127, 'region': 635, 'coord': u'[311, 38, 305]'}, '[143, 41, 310]': {'intensity': 119, 'region': 635, 'coord': u'[143, 41, 310]'}, '[384, 89, 372]': {'intensity': 76, 'region': 635, 'coord': u'[384, 89, 372]'}}


In [34]:
node = sg.nodes()[0]
s = sg.node[node]['coord']
coord = ast.literal_eval(s)
print(s.type)

AttributeError: 'unicode' object has no attribute 'type'

In [55]:
# Getting a subgraph of all the nodes with a certain region
sg = fear.subgraph([n for n, attrdict in fear.node.items() if attrdict['region'] == 0])

In [56]:
print(sg.nodes(data=True))

[('[185, 220, 1]', {'intensity': 57, 'region': 0, 'coord': u'[185, 220, 1]'}), ('[282, 113, 77]', {'intensity': 48, 'region': 0, 'coord': u'[282, 113, 77]'}), ('[225, 222, 120]', {'intensity': 69, 'region': 0, 'coord': u'[225, 222, 120]'}), ('[215, 137, 82]', {'intensity': 41, 'region': 0, 'coord': u'[215, 137, 82]'}), ('[345, 216, 449]', {'intensity': 63, 'region': 0, 'coord': u'[345, 216, 449]'}), ('[363, 153, 416]', {'intensity': 45, 'region': 0, 'coord': u'[363, 153, 416]'}), ('[272, 112, 70]', {'intensity': 44, 'region': 0, 'coord': u'[272, 112, 70]'}), ('[344, 228, 444]', {'intensity': 39, 'region': 0, 'coord': u'[344, 228, 444]'}), ('[215, 234, 74]', {'intensity': 52, 'region': 0, 'coord': u'[215, 234, 74]'}), ('[322, 202, 23]', {'intensity': 51, 'region': 0, 'coord': u'[322, 202, 23]'}), ('[372, 63, 390]', {'intensity': 65, 'region': 0, 'coord': u'[372, 63, 390]'}), ('[206, 245, 41]', {'intensity': 46, 'region': 0, 'coord': u'[206, 245, 41]'}), ('[301, 247, 32]', {'intensity': 

# Getting the dict containing region counts

In [37]:
region_counts = {}
for node in fear.nodes():
    region = fear.node[node]['region']
    if region in region_counts:
        region_counts[region] += 1
    else:
        region_counts[region] = 1

In [101]:
region_centroids = {}
for key in region_counts:
    # Getting a subgraph of all the nodes with a certain region
    region_sg = fear.subgraph([n for n, attrdict in fear.node.items() if attrdict['region'] == key])
    
    total = np.array([0,0,0])
    for node in region_sg.node:
        s = region_sg.node[node]['coord']
        coord = ast.literal_eval(s) # convert string of list to list
        coord = np.array(coord)
        total += coord

    centroid = total / float(nx.number_of_nodes(region_sg))
    region_centroids[key] = centroid

In [102]:
print(ccf[2])

Primary somatosensory area, mouth, layer 6b


In [103]:
print(region_centroids)

{0: array([ 240.86574074,  195.01851852,  187.44907407]), 2: array([ 218. ,  132.5,  161.5]), 7: array([ 226.83333333,  219.83333333,  421.66666667]), 8: array([ 230.93124066,  147.46337818,  269.35874439]), 9: array([ 215.83333333,   72.53333333,  266.46666667]), 10: array([ 236.83870968,   90.61290323,  380.22580645]), 12: array([ 232.,  211.,  337.]), 15: array([ 230.66666667,  166.66666667,  233.        ]), 17: array([ 230.42105263,  108.15789474,  370.94736842]), 19: array([ 229.5 ,  119.5 ,  196.75]), 20: array([ 231.5,  210.5,  309. ]), 23: array([ 195.66666667,  255.2       ,  232.26666667]), 26: array([ 235.13043478,  110.84782609,  373.15217391]), 27: array([ 130.,  152.,  308.]), 28: array([ 251.36363636,  169.18181818,  372.66666667]), 33: array([ 233.69230769,   67.38461538,  362.76923077]), 36: array([  71.,  177.,  183.]), 41: array([ 232.5,   29.5,  376.5]), 42: array([ 205.5,  106.5,  370.5]), 45: array([ 295.,  211.,  444.]), 50: array([ 238.,  126.,  309.]), 52: arra

# Getting the region number -> region name dict

In [44]:
ccf_txt = 'natureCCFOhedited.csv'

ccf = {}
with open(ccf_txt, 'rU') as csvfile:
    csvreader = csv.reader(csvfile)
    for row in csvreader:
        # row[0] is ccf atlas index, row[4] is string of full name
        ccf[int(row[0])] = row[4];
        # print row[0]
        # print row[4]
        # print ', '.join(row)

# Creating the networkx graph of the region centers

In [104]:
g = nx.Graph()

In [105]:
for key, val in region_centroids.iteritems():
    if key in ccf:
        g.add_node(key)
        g.node[key]['coord'] = val
        g.node[key]['name'] = ccf[key]

In [77]:
print(g.nodes(data=True))

[(2, {'name': 'Primary somatosensory area, mouth, layer 6b', 'coord': array([ 240.28571429,   50.14285714,  317.42857143])}), (7, {'name': 'Principal sensory nucleus of the trigeminal', 'coord': array([ 240.28571429,   50.14285714,  317.42857143])}), (8, {'name': 'Basic cell groups and regions', 'coord': array([ 240.28571429,   50.14285714,  317.42857143])}), (9, {'name': 'Primary somatosensory area, trunk, layer 6a', 'coord': array([ 240.28571429,   50.14285714,  317.42857143])}), (10, {'name': 'Superior colliculus, motor related, intermediate gray layer', 'coord': array([ 240.28571429,   50.14285714,  317.42857143])}), (12, {'name': 'Interfascicular nucleus raphe', 'coord': array([ 240.28571429,   50.14285714,  317.42857143])}), (15, {'name': 'Parataenial nucleus', 'coord': array([ 240.28571429,   50.14285714,  317.42857143])}), (17, {'name': 'Superior colliculus, motor related, intermediate white layer', 'coord': array([ 240.28571429,   50.14285714,  317.42857143])}), (19, {'name': 

# Plotting points in a scatterplot

In [106]:
points = []
for node in g.nodes():
    coord = g.node[node]['coord'].tolist()
    name = g.node[node]['name'] 
#     coord.append(name)
    points.append(coord)


points = np.array(points)

In [107]:
print(points)

[[ 218.          132.5         161.5       ]
 [ 226.83333333  219.83333333  421.66666667]
 [ 230.93124066  147.46337818  269.35874439]
 ..., 
 [ 258.33333333   36.88888889  360.33333333]
 [ 211.5         118.5         187.75      ]
 [  60.          110.66666667  210.66666667]]


In [174]:
def generate_pointcloud(thedata, output_path):
    """Generates the plotly from the csv file."""
    # Type in the path to your csv file here
#     thedata = np.genfromtxt(points_path,
#         delimiter=',', dtype='int', usecols = (0,1,2), names=['a','b','c'])
#     thedata = thedata[:,0:3]

    # Set tupleResolution to resolution input parameter
#     tupleResolution = resolution;

    # EG: for Aut1367, the spacing is (0.01872, 0.01872, 0.005).
#     xResolution = tupleResolution[0]
#     yResolution = tupleResolution[1]
#     zResolution = tupleResolution[2]
    # Now, to get the mm image size, we can multiply all x, y, z
    # to get the proper mm size when plotting.

    trace1 = Scatter3d(
        x = thedata[:,0],
        y = thedata[:,1],
        z = thedata[:,2],
        mode='markers',
        marker=dict(
            size=6,
            color='cyan',                # set color to an array/list of desired values
            colorscale='Viridis',   # choose a colorscale
            opacity=0.15
        )
    )

    data = [trace1]
    layout = Layout(
        margin=dict(
            l=0,
            r=0,
            b=0,
            t=0
        ),
        paper_bgcolor='rgb(0,0,0)',
        plot_bgcolor='rgb(0,0,0)'
    )

    fig = Figure(data=data, layout=layout)

    plotly.offline.plot(fig, filename=output_path)

#     plotly.offline.plot(fig, filename= 'output/' + self._token + "/" + self._token + "_brain_pointcloud.html")


In [175]:
generate_pointcloud(points, output_path='Fear199_region_center.html')

# adding adjacency edges to new graph

In [116]:
# flipping dictionary
centroid_to_region = {v.tolist(): k for k, v in region_centroids.iteritems()}

TypeError: unhashable type: 'list'

In [ ]:
for i in range(len(points)):
    pointi = points[i]
    min_dist = float("inf")
    min_point = np.array([])
    for j in range(i + 1, len(points)):
        pointj = points[j]
        dist = numpy.linalg.norm(pointi - pointj)
        if dist < min_dist:
            min_dist = dist
            min_point = pointj
    
    closest


In [161]:
closest_region = {}
for i in range(len(g.nodes())):
    nodei = g.nodes()[i]
    # the coord attribute is stored as a np array
    coordi = g.node[nodei]['coord']
    namei = g.node[nodei]['name'] 
               
    min_dist = float("inf")
    min_point = []
    for j in range(i+1, len(g.nodes())):
        nodej = g.nodes()[j]
        coordj = g.node[nodej]['coord']
        namej = g.node[nodej]['name'] 
        dist = np.linalg.norm(coordi - coordj)
        if dist < min_dist:
            min_dist = dist
            min_point = [namej, dist]
    
    closest_region[namei] = min_point

In [166]:
ge = g.copy()

In [144]:
# flipping ccf dictionary so it goes region name -> region number
ccf_r = {v: k for k, v in ccf.iteritems()}

In [167]:
for key, val in closest_region.iteritems():
    if len(val) == 0:
        continue
    region1 = ccf_r[key]
    region2 = ccf_r[val[0]]
    dist = val[1]
    ge.add_edge(region1, region2, weight=dist)
#     ge.edge[region1][region2]['weight'] = dist

In [173]:
plot_graphml3d(ge, show=False, output_path='Fear199_region_adjacency.html')

In [ ]:
# nx.write_graphml(ge, "Fear199_centers_adjacency.graphml")

In [172]:
# not yet in a .py file
def plot_graphml3d(g, show=False, output_path=None):
    """
    Plotting networkx graph.  output_path should end in '.html'.
    """
    # grab the node positions from the graphML file
    V = nx.number_of_nodes(g)
#     attributes = nx.get_node_attributes(g, 'coord')
    nodes = g.nodes()
    node_positions_3d = pd.DataFrame(columns=['x', 'y', 'z'], index=range(V))
    for i, n in enumerate(nodes):
        coord = g.node[n]['coord']
#         coord = ast.literal_eval()
        node_positions_3d.loc[i] = [coord[0], coord[1], coord[2]]    


    # grab edge endpoints
    edge_x = []
    edge_y = []
    edge_z = []
    
    for e in g.edges():
        # Changing tuple to list
#         source_node = e[0]
#         target_node = e[1]
        
        source_pos = g.node[e[0]]['coord']
        target_pos = g.node[e[1]]['coord']

        edge_x += [source_pos[0], target_pos[0], None]
        edge_y += [source_pos[1], target_pos[1], None]
        edge_z += [source_pos[2], target_pos[2], None]

    # node style
    node_trace = Scatter3d(x=[x for x in node_positions_3d['x']],
                           y=[x for x in node_positions_3d['y']],
                           z=[x for x in node_positions_3d['z']],
                           mode='markers',
                           # name='regions',
                           marker=Marker(symbol='dot',
                                         size=6,
                                         opacity=0.5,
                                         color='purple'),
                           # text=[str(r) for r in range(V)],
                           # text=atlas_data['nodes'],
                           hoverinfo='text')

    # edge style
    edge_trace = Scatter3d(x=edge_x,
                           y=edge_y,
                           z=edge_z,
                           mode='lines',
                           line=Line(color='cyan', width=1),
                           hoverinfo='none')

    # axis style
    axis = dict(showbackground=False,
                showline=False,
                zeroline=False,
                showgrid=False,
                showticklabels=False)

    plot_title = 'graphml plot'
    # overall layout
    layout = Layout(title=plot_title,
                    width=800,
                    height=900,
                    showlegend=False,
                    scene=Scene(xaxis=XAxis(axis),
                                yaxis=YAxis(axis),
                                zaxis=ZAxis(axis)),
                    margin=Margin(t=50),
                    hovermode='closest',
                    paper_bgcolor='rgba(0,0,0,0)',
                    plot_bgcolor='rgb(255,255,255)')

    data = Data([node_trace, edge_trace])
    fig = Figure(data=data, layout=layout)
    if show:
        iplot(fig, validate=False)
    
    if output_path != None:
        plotly.offline.plot(fig, filename=output_path)

# Adjacency Matrix

In [178]:
import connectivity as cn

In [179]:
# Getting the connectivity adjacency matrix
con_adj_mat = nx.adj_matrix(ge).todense()
print(con_adj_mat.shape)
print(con_adj_mat)

(577, 577)
[[   0.            0.            0.         ...,    0.            0.            0.        ]
 [   0.            0.            0.         ...,    0.            0.            0.        ]
 [   0.            0.            0.         ...,    0.            0.            0.        ]
 ..., 
 [   0.            0.            0.         ...,    0.          196.56739687
     0.        ]
 [   0.            0.            0.         ...,  196.56739687    0.
   153.42354683]
 [   0.            0.            0.         ...,    0.          153.42354683
     0.        ]]


In [180]:
fig = cn.plot_con_mat(con_adj_mat, output_path=None, show=True)